In [1]:
import os
import jieba
import jieba.analyse
import pandas as pd
import pyodbc
import configparser
from bs4 import BeautifulSoup
import re
import nltk

In [2]:
config = configparser.ConfigParser()
config.read('config.env')
db_UserName = config.get('DEFAULT', 'DB_USERNAME')
db_Password = config.get('DEFAULT', 'DB_PASSWORD')
db_Name = config.get('DEFAULT', 'DB_NAME')
db_Host = config.get('DEFAULT', 'DB_HOST')

cnxn_str = ("Driver={ODBC Driver 17 for SQL Server};"
            f"Server={db_Host};"
            f"Database={db_Name};"
            f"UID={db_UserName};"
            f"PWD={db_Password};")

cnxn = pyodbc.connect(cnxn_str)
# Create a cursor from the connection
cursor = cnxn.cursor()

In [3]:
# SQL查詢語句
query = ("select source,id,title ,context from ("
         "select a.source,a.id,title,context from pttpost_referendum_4 a "
         " inner join pttpost b on a.source=b.source and a.id=b.Id "
         " where not exists (select * from keyword where source=99 and (b.title like '%'+keyname+'%' or b.context like '%'+keyname+'%')) "
         " union all "
         " select a.source,a.id,title,context from pttpost_referendum_4 a "
         " inner join pttpostgossing b on a.source=b.source and a.id=b.Id "
         " where not exists (select * from keyword where source=99 and (b.title like '%'+keyname+'%' or b.context like '%'+keyname+'%')) "
         " union all "
         " select a.source,convert(varchar,a.id),title,content from dcard.dbo.pttpost_referendum_4 a "
         " inner join dcard.dbo.post b on a.source=b.forum and a.id=b.Id "
         " where not exists (select * from keyword where source=99 and (b.title like '%'+keyname+'%' or b.content like '%'+keyname+'%')) "
         " ) m "
         "where 1=1")

# 讀取資料表
df = pd.read_sql(query, cnxn)

c:\Users\HuanChen\AppData\Local\Programs\Python\Python310\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(


In [4]:
# 載入知網詞庫
jieba.set_dictionary('C:\project\python\dict.big5.txt')

# 載入自定義詞庫
jieba.load_userdict('C:\project\python\main.txt')

Building prefix dict from C:\project\python\dict.big5.txt ...
Loading model from cache C:\Users\HuanChen\AppData\Local\Temp\jieba.u7bf78fb8a3e5c528afaa2a9a1de33675.cache
Loading model cost 0.651 seconds.
Prefix dict has been built successfully.


In [5]:
def get_score(article_string):
    with open('NTUSD_positive_unicode.txt', encoding='utf-8', mode='r') as f:
        positive_words = []
        for l in f:
            positive_words.append(l.strip())

    with open('NTUSD_negative_unicode.txt', encoding='utf-8', mode='r') as f:
        negative_words = []
        for l in f:
            negative_words.append(l.strip())

    score = 0

    if (article_string.strip() != ""):
        jieba_result = jieba.cut(article_string, cut_all=False, HMM=True)

        for word in jieba_result:
            if word.strip() != "":
                if word in positive_words:
                    score += 1
                elif word in negative_words:
                    score -= 1
                else:
                    pass

    return score

In [6]:
# 迴圈處理
try:
    for index, row in df.iterrows():
        context = row["context"]
        # 進行相關處理
        score = get_score(context)
        print(row["id"]+f'總分:{score}')
        if (row["source"]!="talk"):
            sql = "update pttpost_referendum_4 set emotionpost=? where source=? and id=?"
        else:
            sql = "update dcard.dbo.pttpost_referendum_4 set emotionpost=? where source=? and id=?"    
        
        cursor.execute(sql, score, row["source"], row["id"])
        cnxn.commit()
finally:
    cnxn.commit()
    cnxn.close()

M.1609430976.A.8E3總分:0
M.1609433043.A.55E總分:2
M.1609475812.A.E58總分:6
M.1609431119.A.84A總分:1
M.1609493102.A.0D7總分:1
M.1609486228.A.7A7總分:-2
M.1609431922.A.D1B總分:2
M.1609494143.A.E5E總分:3
M.1609487931.A.C53總分:-6
M.1609493527.A.EED總分:1
M.1609558726.A.5F8總分:3
M.1609455786.A.5CD總分:-4
M.1609576721.A.650總分:-2
M.1609501739.A.70D總分:4
M.1609596105.A.6A9總分:-1
M.1609487249.A.3CD總分:9
M.1609490622.A.B0A總分:-2
M.1609475062.A.B64總分:-1
M.1609512481.A.550總分:-1
M.1609598475.A.722總分:1
M.1609505423.A.2F4總分:9
M.1609554561.A.4CF總分:2
M.1609565114.A.031總分:2
M.1609641857.A.217總分:3
M.1609495442.A.758總分:2
M.1609497375.A.B74總分:-2
M.1609584606.A.207總分:-3
M.1609567950.A.BBC總分:-4
M.1609556119.A.E14總分:-5
M.1609516575.A.7ED總分:0
M.1609502938.A.3C6總分:-3
M.1609602476.A.F7B總分:1
M.1609721967.A.496總分:-1
M.1609565905.A.B81總分:-3
M.1609733351.A.BC4總分:0
M.1609571066.A.3D7總分:2
M.1609554769.A.F05總分:-2
M.1609576850.A.681總分:1
M.1609506912.A.D3E總分:3
M.1609559767.A.AE3總分:4
M.1609642073.A.9C7總分:-6
M.1609599419.A.F63總分:-1
M.1609595113.A.F